# ETL das Dimensões - Olist

Este notebook realiza a leitura dos dados brutos (camada Bronze),
armazenados no DBFS, e cria as tabelas dimensão do Data Warehouse
na camada Silver.



In [0]:
#Importações
from pyspark.sql.functions import col, to_timestamp, year, month, dayofmonth


In [0]:
#Paths
BRONZE_PATH = "dbfs:/Workspace/dados_mpv/"


In [0]:
#Leitura dos CSVs (Bronze)
orders_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}olist_orders_dataset.csv")
items_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}olist_order_items_dataset.csv")
products_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}olist_products_dataset.csv")
customers_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}olist_customers_dataset.csv")
sellers_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}olist_sellers_dataset.csv")
category_df = spark.read.option("header", "true").csv(f"{BRONZE_PATH}product_category_name_translation.csv")


In [0]:
# Criar Schema Silver e Gold
spark.sql("CREATE SCHEMA IF NOT EXISTS workspace.silver")
spark.sql("CREATE SCHEMA IF NOT EXISTS workspace.gold")

DataFrame[]

In [0]:
# Dimensão Produto
dim_produto = products_df.join(
    category_df,
    products_df.product_category_name == category_df.product_category_name,
    "left"
).select(
    col("product_id").alias("id_produto"),
    col("product_category_name_english").alias("nome_categoria"),
    col("product_weight_g").alias("peso_produto"),
    col("product_length_cm").alias("comprimento_produto"),
    col("product_height_cm").alias("altura_produto"),
    col("product_width_cm").alias("largura_produto")
).dropDuplicates()

dim_produto.write.mode("overwrite").saveAsTable("silver.dim_produto")


In [0]:
# Dimensão Cliente
dim_cliente = customers_df.select(
    col("customer_id").alias("id_cliente"),
    col("customer_city").alias("cidade_cliente"),
    col("customer_state").alias("estado_cliente")
).dropDuplicates()

dim_cliente.write.mode("overwrite").saveAsTable("silver.dim_cliente")


In [0]:
# Dimensão Vendedor
dim_vendedor = sellers_df.select(
    col("seller_id").alias("id_vendedor"),
    col("seller_city").alias("cidade_vendedor"),
    col("seller_state").alias("estado_vendedor")
).dropDuplicates()

dim_vendedor.write.mode("overwrite").saveAsTable("silver.dim_vendedor")


In [0]:
# Dimensão Data
dim_data = orders_df.withColumn(
    "data", to_timestamp(col("order_purchase_timestamp"))
).select(
    col("order_purchase_timestamp").alias("id_data"),
    col("data"),
    year("data").alias("ano"),
    month("data").alias("mes"),
    dayofmonth("data").alias("dia")
).dropDuplicates()

dim_data.write.mode("overwrite").saveAsTable("silver.dim_data")


In [0]:
# Validação
display(spark.table("silver.dim_produto"))
display(spark.table("silver.dim_cliente"))
display(spark.table("silver.dim_vendedor"))
display(spark.table("silver.dim_data"))


id_produto nome_categoria peso_produto comprimento_produto altura_produto largura_produto 9138555a5066b7f16bf15e75c7db067c construction_tools_lights 540 16 27 16 233ad2cdae25fbf46f0d090b678d23f4 market_place 775 35 9 15 65ae1951caecbb80c7d5e2e662ddb0dc housewares 2700 25 15 25 6831b5d22263248cd732a13b207fd68a toys 400 22 22 22 dfbbf137ccb6af48e66d186a33118579 computers_accessories 450 20 30 30 aceab7cb5e3cc8e531d7e0fc7c4cbffc auto 3400 45 20 45 d3ffe9c4be46e47d76545011a7b37a05 furniture_decor 400 35 10 25 1b06001e6b541c7e43a5a0339129a3ea housewares 1400 30 15 20 7bdcf3299ac200059488f72043f6c3df auto 200 18 10 18 8e71b24c3e25a92fef6176120a67fac7 computers_accessories 783 21 13 28 05696da7eee323669666f62228d00f78 bed_bath_table 12900 60 27 50 5cb1a29179d1883d7ab5424629fe67aa furniture_decor 1100 103 6 20 426c58d69aa402e5397c4b6471420fbe construction_tools_construction 3550 16 105 11 4fd6ec612afa6f67b850b157f00a3368 garden_tools 598 38 30 38 1f14955ab3f179a666e101d5984b1319 fashion_bags_accessories 300 16 8 11 093cd981b714bcdff182b427d87fc8fc sports_leisure 750 16 5 11 4a7dffba3ac0ece48b8fb8511ea672eb watches_gifts 850 48 16 35 d2f5484cbffe4ca766301b21ab9246dd computers_accessories 180 16 9 16 9614dd0585b52cd086cbdcc2dd5fcda4 baby 800 42 25 15 df0c26d7ddb998e2517658a55e46e48a home_appliances_2 14400 55 15 36 7e79042d2bfd50df12f3a4bfff5c43b4 musical_instruments 900 16 6 26 0a904457e165bf24b90921754b4a5888 sports_leisure 1350 31 33 31 0043d1a25ef08fb6f41b8fa6f91742ab construction_tools_construction 20400 30 30 30 afad7a4420a4348d41da23ed8d0902dd furniture_decor 7000 43 35 50 34aec6c5358dee4e71cbaefc14935c5e health_beauty 150 20 10 20 515bd603359b578cf72ec3524f57be73 telephony 200 19 5 20 ff7c7524d5f9a8386ab27088ec03c1fb bed_bath_table 1000 40 10 30 9246f7bd279121747dcb909a41f44df2 bed_bath_table 400 36 6 26 c478b1bbf9ec8c5691f37ccb83187386 computers_accessories 300 25 8 18 8934769521d632e65c27992662f05673 cool_stuff 200 17 4 13 2715967684d6991f7501693bfe08c08b toys 800 28 35 18 0b3c2ee3c7994b5b9ebdddb2372d6f9c bed_bath_table 1250 45 10 15 dbf23e54e9fe684d5774201bdf0de80f housewares 500 20 35 22 da596542f9179c1021970d21d9b53b76 bed_bath_table 750 36 4 29 af1adc5466b28e90f0878a07ef26d3e3 health_beauty 700 16 16 16 e7261ba9b589b73ac45411a15058403e computers_accessories 1600 25 9 25 762e9c384b4752bbcbea568e3d89856f pet_shop 200 21 16 17 b0c89945c034268074f5f80b362bda34 bed_bath_table 550 16 10 16 6a9678c02c9aaec51699e995ab18e48f watches_gifts 333 18 11 12 b12ba6fb4716c6732dc00c5f84466dc8 housewares 11250 38 28 32 79161ecc0839d5d58374918d289ee6c7 health_beauty 125 17 7 12 ab94356394683706626f737b7c135ae1 health_beauty 27050 60 60 45 ce94e3c41145e28428cdae952a1fd7f2 watches_gifts 335 17 11 12 31a3ac2bdbd4af5074e25c5e92ca71ab home_construction 10100 30 61 30 256c61261c818dab727fa2a60d8964ca office_furniture 8638 51 62 26 2a699d35a87e92a01747297243bfc987 sports_leisure 200 18 8 14 67677f0c9d58c64d17cdbad0abe40285 computers_accessories 200 16 4 20 f01058850701fcb9d8f652660012b9ec fashion_shoes 450 29 10 22 092eff69a9499b052a2258f502ea0775 furniture_decor 500 35 8 35 2a7e9f98e73a335bbb0ba2253d0c9b40 auto 8500 65 40 65 31f818fab5ba17c1c2f9b25b33630145 watches_gifts 250 16 10 11 dd68bcbc459a7f8b1e8d41efd8e076b3 stationery 1825 38 21 38 252dc23ff7e1241d046a1c2c5041ffb5 bed_bath_table 1000 43 8 33 8eb0c431f2cf5b2fed9f69a6fd2e8756 telephony 100 19 5 11 f529ca0f6c6d8ea226840a3ffb3109ea stationery 750 25 50 40 65d22d2cf890edf9cfa3bbd5e8cb2371 books_general_interest 400 16 2 11 839321c2db7b3b3eaff4944c3b052ecd housewares 1291 23 23 20 e7a6e03b3e02c37299f6ea8398a08629 auto 150 21 15 14 cc47c0863559499f01b4cad750929d10 cool_stuff 2050 40 40 30 1d9b6ad747838d1e4f24445f4b9bff55 toys 1400 35 28 16 3117617b81eeaddd6d5a788a3d4230f1 small_appliances 100 30 5 11 3625fbaf8284047185fb0351f2f84ae3 sports_leisure 1600 25 8 25 144266e1585320d057797a369596bb8b cool_stuff 1925 30 32 27 0c2ec8ad337c82681af769354356e4c2 furniture_decor 2000 20 65 20 2ef3cc0d3f3adddc0

id_cliente cidade_cliente estado_cliente b776843fdda066d35efda05cc6811dc9 rio de janeiro RJ cea51c6d1ace915c653856b93b4812cf assis SP 860ac166573be76ffb00c3e483892094 belo horizonte MG 33f851c0c106198bcd5a906f28aef4a1 sao luis MA 01cca8f48e415e8612b70b1c5ee759af aracaju SE 47f43c0d4abe700de3511c779bc31f36 curitiba PR 9a0688b0e8ed035cbd5fde3aedc0dbbe sorocaba SP 95df670e57f84a2814b2bc4f6b8cb5f5 cascavel PR f2824bf9bc3ff1facfe05820f06fa436 criciuma SC 55b0a777baab080147369bfa492dbaf6 limeira SP 9f92375d50ab60bcbfcf969aa156d455 fortaleza CE 0f2091dc4350fae3b3ce7b81a55c86b1 salvador BA a411ac48ff9bd97503158c76c67b2af6 nova friburgo RJ 28d5ddbe17cf2c62357a3e08db9d6c47 sao paulo SP 33372bb48ddea1b0e47e44a1b5c72bb1 sao paulo SP 74f84652fb83fc62d4428d8800ac4d4c cascavel PR 6bf5d790b895c0b3dfdbc9b865ac7372 brasilia DF b9cef3a1417192dc00192bb252d3fcab cristalia MG 734d134a571d5b19d6a04edfeee25d93 ribeirao preto SP 6b9f8eca47be692d9b7fb3e1e18b09e6 belem PA 6fb1293bde3b204b920003a3989dbea5 osasco SP 6f47bf761ea5cbc060f0ac4b4fce666e francisco beltrao PR cdf85d0d3bca555a030e00a95504ffca praia grande SP a0e4dd3110c8e935735669706447da3f louveira SP 232fc199e2c1159c64a569a38816e593 sao paulo SP e0b9262d01399885847c98481b33da06 sao paulo SP f0a44676cb97b8d7b986aaea97a53897 araruama RJ dc38adb85ba2eb11bb3cf818834502d2 santo andre SP 115169e81289a703470c78057872755f raposos MG d62aa5699e77744118db71d3f9228dbc sao paulo SP e71debe30488f0d8eac45ecafa13a725 rio de janeiro RJ e60a039c1be831ff11b42d99a76f738f alfenas MG 8725cb0a76a612fb11b5412a07ae98f3 pontal do parana PR 00a16acd591b4bb112f2e94c7d2f9936 sao pedro da aldeia RJ 3598960a3a0a4f66538e48e4335c3e1c juscimeira MT eb12b0442c9bdca72fcfd03a022d71d0 atibaia SP dfeeaacf3ac43668f3a468f71b2cf65b goiania GO 60b2620611c1fd25c9d812a6850fdb4c carinhanha BA 40dab28c1313cba6be3840cd5205ec79 sao miguel do gostoso RN be22f11baf346059cbe6556ef9c69070 porto alegre RS 0a4b13f62e9241a32074e56893ff7b44 engenheiro passos RJ a1746e37af49aa5afd6b195baed286eb cabo frio RJ 26d51363d20344386df9fb922a155a26 lima duarte MG 1d38a317a5e9df61d2bfbebf4cc20068 campos dos goytacazes RJ 4376bf84d8dc27a1b811ee03a0ef7cca aracaju SE e954ac715512f2a20e640cedf80486b5 itapetininga SP 2a3caad976ff659d519660a7c9357122 sombrio SC ab95bb8d3768e62831048ac6e059a973 belo horizonte MG 9e126ac32c9fbec527dc3e9047d2dc7b araguaina TO 409a4744aa5c2af44e194aff56430322 rio de janeiro RJ 0750e4ba17152e6b83cf55f61d391e3b guarulhos SP f4b8696f625adaeef763cc9cd712c921 belem PA 288afe31ee5049731be93138431905a4 sao paulo SP 0df0cc2d605e76a1560ce617738b096d caete MG 428065cc9e87f764effc6d4875c4b4da catalao GO 53798226c7b9a315d93909d3ade79654 sao paulo SP 687f63c64f1b99fbd97d3d1e940c781a juazeiro do norte CE 210ae71748d4491e49ae5fb975f9245d rio de janeiro RJ dcdfe35bfb51be9e9a791431222fb73f sao paulo SP 4f4ed20c56c49d645e19d6e63e37517e rio de janeiro RJ 67dfa1fb67ad51921e5a537ba98c729f juranda PR c5c273dc7587ce40423e6c791c339e79 nova prata do iguacu PR b2df53a0d86cbc9c48616392a6e57c57 mineiros GO 4e2f276c57e614a45ddbd530f67ebfd8 rio de janeiro RJ 8d10d69d2fac34eaff1d041c460d794b sao paulo SP 435f0eb5e9a9002e1bb367ef5fc8317f sao paulo SP df6c931f10ffbf16ec1b2b1056d53f7f curitiba PR 307329610b09cf8c45bec0d871eb1ec8 limeira SP 76ebc39daa5ea881b6ce1ef9554f8b6f londrina PR be6570b98044034f16453eb8281ffa08 rio de janeiro RJ 00a6e2753fc2652cb87386ffbf5792b2 sao paulo SP 47ed96cea4db9f8abefe2a0c30ad997a jundiai SP 6ab85b3fac14f117ea275b5a35503073 vila velha ES e6db53dc3619628a8e024f3e1f4abc86 almenara MG 1ff059c79d3f1d0ee47547940795ed0c brasilia DF 0275161cf1fc69fd8f5412ba423a3004 sao paulo SP b7f5e7be6992f2dbf83cd873e2f8f898 limeira SP 1955d7e0c5a0d6fc2fa2eea4662b8f1f sao jose dos campos SP ac82545ea76f80c8047af33f84a32aff apucarana PR 9f9233b73bc4030c589a0429b3423766 ribeirao preto SP 9466322b97e1ac6b447e2e6404ed612a fazenda rio grande PR f84d0d7ea2cf322d3255ed470e443de5 bom jesus GO 16b1c67999265df183e86f6a29d83626 cariacica ES 5ebc6424b55d612d20110789bbe0d74

id_vendedor cidade_vendedor estado_vendedor e76ecc7e9a1a1e3c6df9d2a8261c423d belo horizonte MG 4cc4fd4fdd406a85bbdc1f824b731bd7 toledo PR ae8bfdbf1c2a2a2dee92d799db0a31c6 toledo PR 478bfe564db21eeb44386606aa30b650 pedro leopoldo MG 99002261c568a84cce14d43fcffb43ea cuiaba MT 83deb69e889cf80f82be1dc6d5f2d486 florianopolis SC 48fb026ed7455a42f5d3e9390ed5088e barra mansa RJ 4e17c65a516f69d023a2ae78b84f28d6 suzano SP 3078096983cf766a32a06257648502d1 scao jose do rio pardo SP d558ebe531605a1285ab2b1bc3256dfb divinopolis MG ad781527c93d00d89a11eecd9dcad7c1 sao jose do rio preto SP 26e13b6ff5b641b329e5524241ee2c93 franca SP 685b870da5b52a710782c9c0fefbeb5b sao bernardo do campo SP e94b64dc6979b302a5a5be1662c83bb6 itapecerica da serra SP 2379bdc3888025689a9deb7b141507d5 mogi mirim SP 999f6d9a1c7c81f43be44c6b7d076210 sao paulo SP afac9f6b0c4e5f0a7ee87e922cd0f873 bauru SP 4a1917ef994878940e1fb03eeb787ad7 brasilia DF dfa0c4c6229ab200a4a1336b4d7128ff florianopolis SC abe021b01ba992245271b9aa422032df curitiba PR 78c99c6dff4eeae5be99bf635ed21e3f marilia SP 3ade81dab5a172b88e1871c28ae05260 sao jose do rio preto SP 0fe2d9733ed841eb064503920015a8c0 ourinhos SP ec8463980a4e0ea9f8517aea1ed0c419 florianopolis SC 276677b5d08786d5dce7c2149dcce48b belo horizonte MG 5e105f5c9f63f5f1fd75d6cb942e55b1 sao jose do rio preto SP 9539213aa8e023c01937bef95dc006da sao paulo SP 81783131d2a97c8d44d406a4be81b5d9 sorocaba SP d4a5e99e0dd915df64ba55a7fbd583fd sao paulo SP 6a8b085f816a1f75f92dbac6eb545f8f bebedouro SP b2bdc5e7940a7d7ca8c4a37953b27a42 vargem grande do sul SP ab91571efab27993ff2f6b36e38055c3 sao paulo SP 38e6dada03429a47197d5d584d793b41 sao paulo SP 07bf9669d84d1f11be443a9dd938f698 sao paulo SP 0f0c984a4a955310903b6b6008660bad franca SP c360e4787614ed31ac7a2f95d3b22dc6 lencois paulista SP 34f563c82a85b99ae9e6d60db5fc2e28 campo bom RS 38874e327ce94d11390b96eb42d61928 itaquaquecetuba SP bba8d0c234a52b87b3957037a215d1a4 goiania GO 578460d8319c51dab351cd9db95eadfe goiania GO cb5df0dcb9e280b1780e9d589889f2c7 bady bassitt SP 3f3486b61f45078d4f31ee5e43d8c5bb sao paulo SP 54965bbe3e4f07ae045b90b0b8541f52 foz do iguacu PR a353b1083c9863d756d9404695016d64 cariacica ES 99cd94252748d2bdde08e17858233602 sao paulo SP f25e239052084705e17a982bc600ab2a sao paulo SP ea846a0e7ad98a741783e886d89dfa44 aracatuba SP eddd1991bd6d9309995a480c39b95137 ponta grossa PR f27e33c6d29b5138fa9967bcd445b6d5 sao paulo SP 44f091b5abab8018f682fce8124b85e5 sao paulo SP 32f1bb9dfa65bc7df5c0d9d95a616be4 sao paulo SP c1f12f926d0ba950578b4fa41115cbb6 sao paulo SP 870d0118f7a9d85960f29ad89d5d989a pocos de caldas MG 11fb6f6d341adbe19e81733701704635 sao paulo SP c33847515fa6305ce6feb1e818569f13 brusque SC db2956745b3a8e9f3785c99f34b5d25e sao sebastiao SP 7a241947449cc45dbfda4f9d0798d9d0 jacutinga MG bdae679a9b282249bc23b9b69dae9a99 brasilia DF e8f6dc8e6a1dcde89d20e3995c8d90b3 sao paulo SP 4978a02ea9c8be7a9b5480680f40334e sao paulo SP 6a8a889bde935bafa76d7848782dfaf9 sao paulo SP 782f78b632a43875dd5b53e3e49c9564 campinas SP b4b447d715f9ab302a188fb43d3e96b3 sao paulo SP cf6f6bc4df3999b9c6440f124fb2f687 sao paulo SP 4200ddf1967c5e41e48db62bc6d4b5ac sao bernardo do campo SP 7e93a43ef30c4f03f38b393420bc753a barueri SP 2305ab43e846518f58dd9d59f3f54e96 sao paulo SP d2572f31e9023e9850ef986a636ff9bf belo horizonte MG 777a0c55737f34ffeb78010f7542ab41 sao paulo SP 9535a841eecebed61a9fb1ac1cbb5597 sao paulo SP 15ead3a5037a918ddb520dfe39a3d2b9 conselheiro lafaiete MG 57a834594e1e9e9219603bfec184eadc santa rosa RS d8bf0fc082fd4a77fc2e5679b6c00133 sao paulo SP 9485a23c0430ba1d58d359391606fce6 santo andre SP 01266d4c46afa519678d16a8b683d325 curitiba PR 768de2a4fc06aacecb9a586ccc30746a brasilia DF 731ef20c231d9a7103a425e83fd91271 lages - sc SC 26b482dccfa29bd2e40703ba45523702 santa barbara d´oeste SP 9aa388272ee334b6ae07bc73706e254a muriae MG d05ae8f7a5bd1d2a690a44cd079e4e27 rio de janeiro RJ 0015a82c2db000af6aaaf3ae2ecb0532 santo andre SP b00af24704019bd2e1b335e70ad11f7c salvador BA 72bc2cce903c872fe376a8faaa81d

id_data data ano mes dia 2018-04-22 23:23:18 2018-04-22T23:23:18.000Z 2018 4 22 2018-06-15 21:45:12 2018-06-15T21:45:12.000Z 2018 6 15 2018-06-10 15:44:20 2018-06-10T15:44:20.000Z 2018 6 10 2017-11-24 23:51:54 2017-11-24T23:51:54.000Z 2017 11 24 2017-08-21 10:33:13 2017-08-21T10:33:13.000Z 2017 8 21 2017-05-23 16:32:06 2017-05-23T16:32:06.000Z 2017 5 23 2018-05-22 14:37:19 2018-05-22T14:37:19.000Z 2018 5 22 2017-11-28 11:14:20 2017-11-28T11:14:20.000Z 2017 11 28 2017-02-17 23:07:09 2017-02-17T23:07:09.000Z 2017 2 17 2017-11-25 11:22:09 2017-11-25T11:22:09.000Z 2017 11 25 2018-01-17 08:21:49 2018-01-17T08:21:49.000Z 2018 1 17 2018-03-06 00:42:20 2018-03-06T00:42:20.000Z 2018 3 6 2018-08-28 09:18:17 2018-08-28T09:18:17.000Z 2018 8 28 2017-04-12 10:59:59 2017-04-12T10:59:59.000Z 2017 4 12 2018-06-25 12:06:07 2018-06-25T12:06:07.000Z 2018 6 25 2018-03-08 16:07:39 2018-03-08T16:07:39.000Z 2018 3 8 2017-05-27 00:55:16 2017-05-27T00:55:16.000Z 2017 5 27 2018-05-17 18:33:00 2018-05-17T18:33:00.000Z 2018 5 17 2017-05-30 09:39:34 2017-05-30T09:39:34.000Z 2017 5 30 2018-01-01 20:11:53 2018-01-01T20:11:53.000Z 2018 1 1 2018-02-05 19:25:42 2018-02-05T19:25:42.000Z 2018 2 5 2018-01-23 11:51:03 2018-01-23T11:51:03.000Z 2018 1 23 2018-08-12 23:29:24 2018-08-12T23:29:24.000Z 2018 8 12 2017-01-31 00:53:39 2017-01-31T00:53:39.000Z 2017 1 31 2017-04-06 10:50:06 2017-04-06T10:50:06.000Z 2017 4 6 2018-02-26 17:35:23 2018-02-26T17:35:23.000Z 2018 2 26 2017-12-19 16:03:33 2017-12-19T16:03:33.000Z 2017 12 19 2018-02-26 18:53:26 2018-02-26T18:53:26.000Z 2018 2 26 2017-05-02 16:27:09 2017-05-02T16:27:09.000Z 2017 5 2 2016-10-04 14:13:22 2016-10-04T14:13:22.000Z 2016 10 4 2018-02-09 17:42:05 2018-02-09T17:42:05.000Z 2018 2 9 2017-11-23 16:21:25 2017-11-23T16:21:25.000Z 2017 11 23 2018-02-20 10:45:27 2018-02-20T10:45:27.000Z 2018 2 20 2017-04-20 11:33:57 2017-04-20T11:33:57.000Z 2017 4 20 2017-05-26 09:19:13 2017-05-26T09:19:13.000Z 2017 5 26 2018-02-02 17:52:04 2018-02-02T17:52:04.000Z 2018 2 2 2017-12-11 15:00:24 2017-12-11T15:00:24.000Z 2017 12 11 2018-03-14 08:45:03 2018-03-14T08:45:03.000Z 2018 3 14 2017-10-24 10:24:30 2017-10-24T10:24:30.000Z 2017 10 24 2017-12-27 12:36:41 2017-12-27T12:36:41.000Z 2017 12 27 2017-09-08 17:21:34 2017-09-08T17:21:34.000Z 2017 9 8 2018-07-12 15:03:20 2018-07-12T15:03:20.000Z 2018 7 12 2018-03-13 14:16:30 2018-03-13T14:16:30.000Z 2018 3 13 2018-04-29 15:52:00 2018-04-29T15:52:00.000Z 2018 4 29 2018-06-29 19:03:28 2018-06-29T19:03:28.000Z 2018 6 29 2018-05-10 18:27:34 2018-05-10T18:27:34.000Z 2018 5 10 2017-03-13 17:03:55 2017-03-13T17:03:55.000Z 2017 3 13 2018-03-11 22:13:55 2018-03-11T22:13:55.000Z 2018 3 11 2018-01-24 11:40:54 2018-01-24T11:40:54.000Z 2018 1 24 2018-06-16 11:12:18 2018-06-16T11:12:18.000Z 2018 6 16 2018-01-29 00:32:29 2018-01-29T00:32:29.000Z 2018 1 29 2018-03-23 08:49:19 2018-03-23T08:49:19.000Z 2018 3 23 2018-05-08 20:28:49 2018-05-08T20:28:49.000Z 2018 5 8 2017-05-30 15:08:01 2017-05-30T15:08:01.000Z 2017 5 30 2017-03-16 20:04:07 2017-03-16T20:04:07.000Z 2017 3 16 2017-12-16 15:51:16 2017-12-16T15:51:16.000Z 2017 12 16 2017-11-26 16:15:10 2017-11-26T16:15:10.000Z 2017 11 26 2018-01-29 13:35:39 2018-01-29T13:35:39.000Z 2018 1 29 2017-03-14 16:25:43 2017-03-14T16:25:43.000Z 2017 3 14 2017-08-04 18:26:41 2017-08-04T18:26:41.000Z 2017 8 4 2018-07-18 19:20:21 2018-07-18T19:20:21.000Z 2018 7 18 2018-08-12 19:29:47 2018-08-12T19:29:47.000Z 2018 8 12 2018-02-19 09:07:09 2018-02-19T09:07:09.000Z 2018 2 19 2018-05-14 12:47:30 2018-05-14T12:47:30.000Z 2018 5 14 2018-05-16 23:04:37 2018-05-16T23:04:37.000Z 2018 5 16 2018-01-28 19:34:50 2018-01-28T19:34:50.000Z 2018 1 28 2017-01-27 10:29:59 2017-01-27T10:29:59.000Z 2017 1 27 2018-08-07 22:32:02 2018-08-07T22:32:02.000Z 2018 8 7 2017-07-17 09:29:02 2017-07-17T09:29:02.000Z 2017 7 17 2018-01-31 14:16:10 2018-01-31T14:16:10.000Z 2018 1 31 2017-03-02 01:37:02 2017-03-02T01:37:02.000Z 2017 3 2 2017-12-27 22:41:49 2017-12-27T22:41:49.000Z 2017 12 27 2018-03-12 15:01:

In [0]:
spark.sql("SHOW TABLES IN workspace.silver").show()


+--------+------------+-----------+
|database|   tableName|isTemporary|
+--------+------------+-----------+
|  silver| dim_cliente|      false|
|  silver|    dim_data|      false|
|  silver| dim_produto|      false|
|  silver|dim_vendedor|      false|
+--------+------------+-----------+

